# Assignment

In [4]:
# Import 

import numpy as np
import matplotlib.pyplot as plt
import numpy.matlib
import pandas as pd
from degree_freedom_queen import *
from degree_freedom_king1 import *
from degree_freedom_king2 import *
from generate_game import *
from Chess_env import *
import random

size_board = 4
## INITIALISE THE ENVIRONMENT

env=Chess_Env(size_board)

## The Environment

You can find the environment in the file Chess_env, which contains the class Chess_env. To define an object, you need to provide the board size considered as input. In our example, size_board=4. 
Chess_env is composed by the following methods:

1. Initialise_game. The method initialises an episode by placing the three pieces considered (Agent's king and queen, enemy's king) in the chess board. The outputs of the method are described below in order.

     S $\;$ A matrix representing the board locations filled with 4 numbers: 0, no piece in that position; 1, location of the 
     agent's king; 2 location of the queen; 3 location of the enemy king.
     
     X $\;$ The features, that is the input to the neural network. See the assignment for more information regarding the            definition of the features adopted. To personalise this, go into the Features method of the class Chess_env() and change        accordingly.
     
     allowed_a $\;$ The allowed actions that the agent can make. The agent is moving a king, with a total number of 8                possible actions, and a queen, with a total number of $(board_{size}-1)\times 8$ actions. The total number of possible actions correspond      to the sum of the two, but not all actions are allowed in a given position (movements to locations outside the borders or      against chess rules). Thus, the variable allowed_a is a vector that is one (zero) for an action that the agent can (can't)      make. Be careful, apply the policy considered on the actions that are allowed only.
     

2. OneStep. The method performs a one step update of the system. Given as input the action selected by the agent, it updates the chess board by performing that action and the response of the enemy king (which is a random allowed action in the settings considered). The first three outputs are the same as for the Initialise_game method, but the variables are computed for the position reached after the update of the system. The fourth and fifth outputs are:

     R $\;$ The reward. To change this, look at the OneStep method of the class where the rewards are set.
     
     Done $\;$ A variable that is 1 if the episode has ended (checkmate or draw).
     
     
3. Features. Given the chessboard position, the method computes the features.

This information and a quick analysis of the class should be all you need to get going. The other functions that the class exploits are uncommented and constitute an example on how not to write a python code. You can take a look at them if you want, but it is not necessary.






In [54]:
##  Define functions

def EpsilonGreedy_Policy(Qvalues, epsilon, allowed_a):
    
    N_a=np.shape(Qvalues)[0]
    a = list(range(0, N_a))
    a = [i for idx, i in enumerate(a) if allowed_a[idx]]
    Qvalues = [i for idx, i in enumerate(Qvalues) if allowed_a[idx]]

    rand_value=np.random.uniform(0,1)
 ## epsilon is probability that we go random
    rand_a=rand_value<epsilon

    if rand_a==True:
        
        a = random.choice(a)

    else:
        idx=np.argmax(Qvalues)
        a = a[idx]
            
    return a


def ComputeQvalues(W1, W2, bias_W1, bias_W2, X, hiddenactivfunction , outeractivfunction):
    ## Qvalues=np.matmul(W2, np.matmul(W1,X)) ## this is direct computation of hidden layer and then output layer, without applying any non linear activation function
    ## below is a better solution:
    # Neural activation: input layer -> hidden layer
    H1 = np.matmul(W1,X)+bias_W1 ## make sure that bias_W1 does not need to be transposed
    # if hidden activ function is given:
    if (hiddenactivfunction == 1):
        H1 = np.round(1/(1+np.exp(-H1)), 5)
        
    Qvalues = np.matmul(W2,H1) + bias_W2
    
    #if outer activ function is given
    if (outeractivfunction == 1):
        Qvalues = np.round(1/(1+np.exp(- Qvalues)), 5)

    return Qvalues


In [55]:
# INITIALISE THE PARAMETERS OF YOUR NEURAL NETWORK AND...
# PLEASE CONSIDER TO USE A MASK OF ONE FOR THE ACTION MADE AND ZERO OTHERWISE IF YOU ARE NOT USING VANILLA GRADIENT DESCENT...
# WE SUGGEST A NETWORK WITH ONE HIDDEN LAYER WITH SIZE 200. 


S,X,allowed_a=env.Initialise_game()



N_a=np.shape(allowed_a)[0]   # TOTAL NUMBER OF POSSIBLE ACTIONS
N_in=np.shape(X)[0]    ## INPUT SIZE
N_h=200                ## NUMBER OF HIDDEN NODES



## INITALISE YOUR NEURAL NETWORK... Here weights from input to hidden layer and from the hidden layer to output layer are initialized
W1=np.random.randn(N_h,N_in)/1000
W2=np.random.randn(N_a,N_h)/1000


##W1 = np.divide(W1,np.matlib.repmat(np.sum(W1,1)[:,None],1,N_in))
##W2 = np.divide(W2,np.matlib.repmat(np.sum(W2,1)[:,None],1,N_h))


bias_W1 = np.zeros((N_h,))

bias_W2 = np.zeros((N_a,))



# HYPERPARAMETERS SUGGESTED (FOR A GRID SIZE OF 4)

epsilon_0 = 0.2     # STARTING VALUE OF EPSILON FOR THE EPSILON-GREEDY POLICY
beta = 0.005      # THE PARAMETER SETS HOW QUICKLY THE VALUE OF EPSILON IS DECAYING (SEE epsilon_f BELOW)
gamma = 0.85        # THE DISCOUNT FACTOR
eta = 0.0035        # THE LEARNING RATE

N_episodes = 1000 # THE NUMBER OF GAMES TO BE PLAYED 

hiddenactivfunction = 0
outeractivfunction = 0

# SAVING VARIABLES
R_save = np.zeros([N_episodes, 1])
N_moves_save = np.zeros([N_episodes, 1])


In [ ]:
# SARSA

for n in range(N_episodes):
    S,X,allowed_a=env.Initialise_game()
   
    epsilon_f = epsilon_0 / (1 + beta * n)   ## DECAYING EPSILON
    Done=0                                   ## SET DONE TO ZERO (BEGINNING OF THE EPISODE)
    i = 1                                    ## COUNTER FOR NUMBER OF ACTIONS
                               
    Qvalues = ComputeQvalues(W1, W2, bias_W1, bias_W2, X, hiddenactivfunction , outeractivfunction)

    
    a=EpsilonGreedy_Policy(Qvalues,epsilon_f, allowed_a)
    
    while (Done==0 and i<50):                           ## START THE EPISODE
       
        Qvalues = ComputeQvalues(W1, W2, bias_W1, bias_W2, X, hiddenactivfunction , outeractivfunction)   
        print(Qvalues)
        S_next, X_next,allowed_a_next,R,Done=env.OneStep(a)
        
        ## THE EPISODE HAS ENDED, UPDATE...BE CAREFUL, THIS IS THE LAST STEP OF THE EPISODE
        if Done==1:
            R_save[n,]=np.copy(R)
            #print(i)
            N_moves_save[n,]=i
            dEdQ=R-Qvalues[a]
           
          
            ## update W2 and B2   
            dQdY = 1  
            if outeractivfunction == 1:
                    dYdQ = Qvalues[a]*(1-Qvalues[a])
                    
          
            H = np.matmul(W1,X) + bias_W1
            if hiddenactivfunction == 1:
                     H = np.round(1/(1+np.exp(-H)), 5)
            dYdW = H
    
        
            W2[a,:]=W2[a,:]+eta*dEdQ*dQdY*dYdW
            bias_W2[a]=bias_W2[a]+eta*dEdQ*dQdY
            
            
             ## update W1 and B1 after W2 and B2 were updated
        
            if hiddenactivfunction == 1:
                dYdZ =  (W2[a,:].reshape(1, 200) * H*(1-H).reshape(1, 200)).reshape(200,1)
            else:
                 dYdZ =  W2[a,:].reshape(200, 1)
        
            dZDW = X.reshape(1, 58)        
            W1[:,:]=W1[:,:]+ eta*dEdQ*dQdY*dYdZ*dZDW 
            bias_W1=bias_W1+ eta*dEdQ*dQdY*dYdZ.reshape(200,) 
            
            break
        
       
  
        
        
        # IF THE EPISODE IS NOT OVER...
        else:
            
            Qvalues1=ComputeQvalues(W1, W2, bias_W1, bias_W2, X_next, hiddenactivfunction , outeractivfunction)
            
            a1=EpsilonGreedy_Policy(Qvalues1,epsilon_f, allowed_a_next)

            # Compute the delta
         
            dEdQ=R+gamma*1 - Qvalues1[a1]- Qvalues[a]
                  
            ## update W2 and B2   
            dQdY = 1  
            if outeractivfunction == 1:
                    dYdQ = Qvalues[a]*(1-Qvalues[a])
                    
          
            H = np.matmul(W1,X) + bias_W1
            if hiddenactivfunction == 1:
                     H = np.round(1/(1+np.exp(-H)), 5)
            dYdW = H
    
        
            W2[a,:]=W2[a,:]+eta*dEdQ*dQdY*dYdW
            bias_W2[a]=bias_W2[a]+eta*dEdQ*dQdY
            
            
             ## update W1 and B1 after W2 and B2 were updated
        
            if hiddenactivfunction == 1:
                dYdZ =  (W2[a,:].reshape(1, 200) * H*(1-H).reshape(1, 200)).reshape(200,1)
            else:
                 dYdZ =  W2[a,:].reshape(200, 1)
        
            dZDW = X.reshape(1, 58)        
            W1[:,:]=W1[:,:]+ eta*dEdQ*dQdY*dYdZ*dZDW 
            bias_W1=bias_W1+ eta*dEdQ*dQdY*dYdZ.reshape(200,) 
            
        # NEXT STATE AND CO. BECOME ACTUAL STATE...     
        S=np.copy(S_next)
        X=np.copy(X_next)
        a = np.copy(a1)

        i += 1  # UPDATE COUNTER FOR NUMBER OF ACTIONS

        
        
    
    

[ 3.42972661e-05 -4.16384303e-05  2.88895887e-05 -6.63429835e-05
 -2.26980343e-06  2.75718821e-05  5.93088159e-05  8.45242617e-06
  1.82905572e-05 -5.26447652e-06 -1.76918547e-05  7.25697436e-06
 -2.64834933e-05  1.01690593e-05  1.46113446e-05 -4.44913570e-05
  2.33117454e-05  5.19886539e-05  3.44109805e-05  2.13874647e-05
 -6.38205294e-05 -1.01233279e-05  4.99719106e-05 -3.84881033e-05
  7.26311287e-05 -8.77856024e-06 -5.03876908e-05  1.15057282e-05
 -5.44976075e-05  8.60542555e-06 -8.49367197e-06 -1.26312824e-05]
[ 3.07231791e-05 -2.82582253e-05  1.77240180e-05 -1.33598828e-05
  1.81061800e-05  5.02716109e-05  5.45561714e-05  1.64221719e-05
  3.72642216e-06  1.26083679e-05  1.71498433e-05 -3.49233004e-05
 -2.15375365e-06 -5.04485932e-06 -2.30370068e-06 -1.58259840e-05
  2.68447843e-05 -5.67273801e-06  6.29245994e-05 -3.35874354e-05
 -7.50859970e-05 -3.19018546e-05  6.62628427e-05 -3.29580285e-05
  2.99169644e-03  1.96278498e-05 -5.36821752e-05  3.90843339e-05
 -4.75088113e-06  1.8454

[-1.64285426e-05 -4.46878855e-05  5.99825534e-06  8.70724100e-03
 -6.02977908e-06  3.79621111e-05  4.66066990e-06 -2.14509139e-05
  2.89361710e-05  9.40706420e-06  4.26190309e-05  7.60154820e-06
  8.55889987e-06  7.57565700e-06  1.02419953e-05 -5.58883442e-05
  8.82993051e-03  2.43578311e-05  1.46443133e-02 -3.47571526e-05
 -3.13994780e-05  2.92055756e-03 -9.65226551e-06  2.82120232e-06
  5.09389767e-02  4.49321835e-02  2.85074456e-03  8.81551142e-03
 -2.02019514e-05  2.55628930e-05 -6.06695097e-05  2.96716787e-03]
[ 2.78058186e-05 -4.93163173e-05  2.34061944e-05  8.64730977e-03
 -3.20250476e-05  1.30879704e-05  3.31511805e-05 -3.03197977e-05
  2.87445405e-06 -1.12994805e-05  6.74701694e-06 -9.15688507e-06
  1.40550780e-05  2.38847018e-05  2.53402774e-05  2.75657033e-03
  8.81463328e-03  1.41162562e-05  1.46175037e-02  2.49191785e-05
 -6.37604377e-05  2.93143166e-03  2.13711503e-05 -3.91365517e-05
  5.09253379e-02  4.49286091e-02  2.86681883e-03  8.80798310e-03
 -2.73395836e-05  3.4819

[ 3.40505045e-05  2.70319970e-03 -9.75183938e-08  1.16333393e-02
  3.54299526e-05  4.26384929e-05 -3.17106339e-05  8.96616508e-06
 -2.59645219e-05  5.37099734e-03  3.73189717e-05  2.06823363e-05
  3.11239965e-06  3.63832243e-05 -2.14392082e-05  2.84655938e-03
  8.83969934e-03  5.00411917e-05  2.00668184e-02  8.66481271e-06
 -2.77233420e-05  2.91810125e-03  1.81549414e-05  4.66742057e-05
  9.60839816e-02  9.26579471e-02  2.86929524e-03  1.44566679e-02
 -3.58915676e-05  2.02319763e-05  1.13422472e-05  2.93460400e-03]
[-6.12734011e-06  2.69261275e-03  1.27158665e-05  1.16341142e-02
 -1.89787560e-06 -7.66326119e-06 -3.92742108e-05 -5.01584078e-05
 -3.26417605e-06  5.38885066e-03  4.73584405e-05  2.62851144e-05
  8.45138823e-05  5.69656161e-05  2.35223871e-05  2.81750858e-03
  8.81321907e-03 -7.74876027e-07  2.00441021e-02  5.38656313e-07
 -1.04634645e-05  2.92373930e-03 -5.51143255e-06  7.77348443e-06
  9.83951546e-02  9.26473342e-02  2.92297329e-03  1.44062096e-02
  8.37762854e-06  1.7767

[ 5.74970129e-03  2.68211699e-03  1.79051210e-05  2.20586428e-02
  2.66800490e-03  3.50812480e-05 -2.87901230e-05 -3.08626423e-05
 -2.39175790e-05  5.36532100e-03 -2.40718321e-06 -1.16031380e-05
  3.95231152e-05  2.56271977e-05 -4.81055662e-06  5.77184001e-03
  1.13916595e-02  4.00742948e-05  2.58059562e-02 -4.27183401e-05
 -4.74856410e-05  2.90864005e-03  3.93964496e-06  1.75373312e-05
  1.40902677e-01  1.22864148e-01  2.88469978e-03  3.58542870e-02
 -3.34114784e-05  2.49243119e-05  3.44134291e-05  5.57044162e-03]
[ 5.78641844e-03  2.73086829e-03  4.42062602e-05  2.45203144e-02
  2.67977535e-03  1.07644319e-05  3.87218201e-05  4.54006789e-06
  2.63600626e-05  5.31556858e-03 -5.45241280e-07  1.79783683e-05
 -3.74345929e-06 -1.05723971e-05 -7.69069841e-06  5.68218134e-03
  1.13897293e-02  4.15198862e-05  2.58452121e-02  1.87539218e-05
 -2.59818642e-05  2.95256572e-03  2.95164914e-05 -4.28884978e-05
  1.40889239e-01  1.22842799e-01  2.85385566e-03  3.58359170e-02
 -5.54666180e-05 -8.8000

[ 5.73634179e-03  2.76845691e-03  3.65476941e-05  3.49944123e-02
  2.70503734e-03  4.16124078e-05  3.47414226e-05  5.38252346e-06
  3.01410348e-05  7.77589576e-03  2.41562085e-05  3.48876664e-03
  5.41284972e-03 -2.23998269e-06  3.12292046e-05  8.65831490e-03
  1.13876080e-02 -2.43986351e-05  2.86264891e-02 -2.34327833e-05
 -1.32002195e-05  2.94622051e-03  5.65058542e-05 -7.18781139e-05
  1.81300037e-01  1.64283579e-01  7.81103769e-03  3.81761051e-02
  2.43289089e-03 -3.02046217e-05 -1.70488320e-05  7.94586825e-03]
[ 5.79341444e-03  2.73455960e-03  3.86273325e-05  3.49259789e-02
  2.63863970e-03  2.26385917e-05  5.30673178e-05  1.37996150e-05
  1.02541792e-05  7.70257451e-03  1.96665961e-05  3.52633680e-03
  5.38121907e-03 -1.19454665e-05  1.91402843e-05  8.63672025e-03
  1.13888344e-02  4.10803539e-05  2.85907602e-02  2.05623925e-05
 -4.05855006e-05  2.93411032e-03  4.91945113e-05 -3.02086261e-05
  1.83609190e-01  1.64320745e-01  7.81225828e-03  3.81733829e-02
  2.38406140e-03 -2.3768

...

[7.45979811e-02 3.11837593e-02 1.12951675e-02 2.38238533e-01
 5.00440984e-02 1.33134918e-02 4.84746205e-02 3.13019430e-02
 9.31549500e-03 8.38753148e-02 5.55011978e-02 2.01999428e-02
 4.73440830e-02 6.95302248e-05 3.21577401e-03 6.15320569e-02
 3.07800352e-02 4.52942960e-03 8.43944184e-02 1.11066312e-02
 6.92986171e-03 6.28851072e-02 2.16395055e-02 1.48055383e-02
 4.83668484e-01 3.66858526e-01 1.56802702e-01 3.98936963e-01
 4.76098653e-02 4.39239873e-02 4.46270921e-02 4.87545077e-02]
[7.45778878e-02 3.11970451e-02 1.13287914e-02 2.38252782e-01
 5.00331022e-02 1.32910971e-02 4.84907819e-02 3.13162662e-02
 9.33590053e-03 8.38559017e-02 5.55257885e-02 2.02034987e-02
 4.73713324e-02 3.61963584e-05 3.20549300e-03 6.14883233e-02
 3.07606463e-02 4.48475345e-03 8.44001254e-02 1.10788079e-02
 6.88751980e-03 6.28766770e-02 2.16533417e-02 1.47737841e-02
 4.83648491e-01 3.67210258e-01 1.56769975e-01 3.98949214e-01
 4.76590104e-02 4.39098365e-02 4.46229086e-02 4.87625454e-02]
[7.46335952e-02 3.1210

[7.46186960e-02 3.12329591e-02 1.13024409e-02 2.39794203e-01
 5.00723820e-02 1.32684583e-02 4.85495267e-02 3.13010305e-02
 9.34849526e-03 8.38379810e-02 5.55393073e-02 2.01719909e-02
 4.74293549e-02 2.17586406e-05 3.21662002e-03 6.15100055e-02
 3.07544005e-02 4.43854637e-03 8.44199407e-02 1.11027965e-02
 6.93335626e-03 6.29612967e-02 2.16625567e-02 1.47337506e-02
 4.80610496e-01 3.66485488e-01 1.56772595e-01 4.01695314e-01
 4.76924598e-02 4.39286805e-02 4.46483877e-02 4.88018915e-02]
[ 7.46196417e-02  3.12720643e-02  1.12970533e-02  2.39733260e-01
  5.00335278e-02  1.32741976e-02  4.86092144e-02  3.13422458e-02
  9.37536802e-03  8.38510692e-02  5.55756398e-02  2.01951016e-02
  4.73798338e-02 -2.49210075e-06  3.20583507e-03  6.15252953e-02
  3.07381679e-02  4.48133262e-03  8.44046113e-02  1.11354904e-02
  6.99305119e-03  6.29369306e-02  2.17012736e-02  1.46720628e-02
  4.80721429e-01  3.66490779e-01  1.56752314e-01  4.01735099e-01
  4.76268953e-02  4.38801648e-02  4.46400306e-02  4.8810

[ 7.60872771e-02  3.12905347e-02  1.13515626e-02  2.41910219e-01
  5.00420496e-02  1.56710670e-02  4.86035391e-02  3.41710161e-02
  9.41896903e-03  8.38646991e-02  5.88966045e-02  2.02426106e-02
  4.73917093e-02 -1.31547118e-05  3.21550851e-03  6.14767330e-02
  3.23755647e-02  4.47479704e-03  8.44290355e-02  1.11704330e-02
  6.93972904e-03  6.29476414e-02  2.16972332e-02  1.46993964e-02
  4.77833230e-01  3.65927030e-01  1.58797859e-01  4.01079636e-01
  4.76403679e-02  4.38879836e-02  4.46460240e-02  4.88532307e-02]
[7.61025298e-02 3.12931214e-02 1.13512078e-02 2.42088151e-01
 5.01279077e-02 1.56936025e-02 4.85915084e-02 3.41622067e-02
 9.38936520e-03 8.39367722e-02 5.88927324e-02 2.02120506e-02
 4.74537904e-02 1.60911297e-05 3.24142066e-03 6.15528684e-02
 3.23686449e-02 4.44352533e-03 8.44830255e-02 1.11073588e-02
 6.94853069e-03 6.29905408e-02 2.17025800e-02 1.47032126e-02
 4.77912954e-01 3.66001180e-01 1.58926854e-01 4.01164329e-01
 4.76855139e-02 4.39330161e-02 4.46605235e-02 4.8862

[ 7.60781461e-02  3.12877184e-02  1.13363283e-02  2.41974077e-01
  5.01037968e-02  1.56842369e-02  4.85716844e-02  3.41936418e-02
  9.33507262e-03  8.39210971e-02  5.89311587e-02  2.01768547e-02
  4.73790296e-02 -1.05206600e-05  3.20485674e-03  6.15102361e-02
  3.35482456e-02  4.44761682e-03  8.58323926e-02  1.11348702e-02
  6.96703225e-03  6.29656739e-02  2.17044584e-02  1.46962825e-02
  4.79042224e-01  3.66820408e-01  1.58774674e-01  4.01998028e-01
  4.90868520e-02  4.39069870e-02  4.46135824e-02  4.88214053e-02]
[ 7.60862851e-02  3.12760387e-02  1.13338812e-02  2.41924831e-01
  5.00518461e-02  1.56668968e-02  4.85802214e-02  3.41736828e-02
  9.31670710e-03  8.38888092e-02  5.89079037e-02  2.02030892e-02
  4.74029897e-02 -1.00330870e-06  3.25624829e-03  6.15161537e-02
  3.35552515e-02  4.46162708e-03  8.57935533e-02  1.11021633e-02
  6.90606758e-03  6.29659368e-02  2.16936836e-02  1.47342169e-02
  4.78856472e-01  3.66795026e-01  1.58770849e-01  4.02080607e-01
  4.91011294e-02  4.3912

[7.60457741e-02 3.12359535e-02 1.13452159e-02 2.42821816e-01
 5.00956899e-02 1.56816305e-02 4.84703241e-02 3.41493384e-02
 9.30284408e-03 8.39018126e-02 6.02200889e-02 2.02359133e-02
 4.73652143e-02 4.18589315e-05 3.20861754e-03 6.15331439e-02
 3.35651132e-02 4.50419906e-03 8.68400539e-02 1.11393507e-02
 6.93379961e-03 6.29594344e-02 2.16371528e-02 1.47790251e-02
 4.83503189e-01 3.68340742e-01 1.63898915e-01 4.06318482e-01
 4.90391502e-02 4.39353614e-02 4.57808859e-02 4.88114457e-02]
[7.60284757e-02 3.12523093e-02 1.13591365e-02 2.42805062e-01
 5.00785216e-02 1.56749777e-02 4.84936490e-02 3.41551740e-02
 9.30971434e-03 8.39329551e-02 6.02502517e-02 2.02324753e-02
 4.74342934e-02 3.63385965e-05 3.25420246e-03 6.15380735e-02
 3.35411331e-02 4.46224395e-03 8.68094072e-02 1.11167240e-02
 6.92520484e-03 6.29172189e-02 2.16881119e-02 1.47304981e-02
 4.83669900e-01 3.68361215e-01 1.64892371e-01 4.06441355e-01
 4.90963671e-02 4.39172075e-02 4.57692941e-02 4.88273240e-02]
[7.60464672e-02 3.1236

In [ ]:
# Plot the performance
N_moves_save = pd.DataFrame(N_moves_save, columns = ['N_moves'])
N_moves_save['N_moves'] = N_moves_save['N_moves'].ewm(span=100, adjust=False).mean()


plt.plot(N_moves_save['N_moves'])
plt.xlabel('Episodes')
plt.ylabel('Number of Steps until Done')
plt.title('Average number of steps until Done per Episode')
plt.show()

R_save = pd.DataFrame(R_save, columns = ['R_save'])
R_save['R_save'] = R_save['R_save'].ewm(span=100, adjust=False).mean()

plt.plot(R_save)
plt.xlabel('Episodes')
plt.ylabel('Reward')
plt.title('Average Rewards per Episode')
plt.show()

In [13]:
# Q -learning

for n in range(N_episodes):
    S,X,allowed_a=env.Initialise_game()
    epsilon_f = epsilon_0 / (1 + beta * n)   ## DECAYING EPSILON
    Done=0                                   ## SET DONE TO ZERO (BEGINNING OF THE EPISODE)
    i = 1                                    ## COUNTER FOR NUMBER OF ACTIONS
    
  
    
    while (Done==0 and i<50):                           ## START THE EPISODE
       
        Qvalues = ComputeQvalues(W1, W2, bias_W1, bias_W2, X, activfunction)  
        a=EpsilonGreedy_Policy(Qvalues,epsilon_f, allowed_a)
        S_next, X_next,allowed_a_next,R,Done=env.OneStep(a)
        
        ## THE EPISODE HAS ENDED, UPDATE...BE CAREFUL, THIS IS THE LAST STEP OF THE EPISODE
        if Done==1:
            R_save[n,]=np.copy(R)
            print(i)
            N_moves_save[n,]=i
            print(N_moves_save[n,])
            
            delta=R-Qvalues[a]
            H = np.matmul(W1,X)+bias_W1
            W2[a,:]=W2[a,:]+eta*delta*H
            
            delta =  W2[a,:].reshape(200, 1)*X.reshape(1, 58)
            W1[:,:]=W1[:,:]+ eta*delta
        
            
            ## TO DO: update biases 
            break
       
  
        
        
        # IF THE EPISODE IS NOT OVER...
        else:
            
            Qvalues1=ComputeQvalues(W1, W2, bias_W1, bias_W2, X_next, activfunction)
            a1=EpsilonGreedy_Policy(Qvalues1,0, allowed_a_next)

            # Compute the delta
            delta=R+gamma*Qvalues1[a1]-Qvalues[a]

            # Update the weights
            H = np.matmul(W1,X)+bias_W1
            W2[a,:]=W2[a,:]+eta*delta*H
            
            delta =  W2[a,:].reshape(200, 1)*X.reshape(1, 58)
            W1[:,:]=W1[:,:]+ eta*delta
            
        # NEXT STATE AND CO. BECOME ACTUAL STATE...     
        S=np.copy(S_next)
        X=np.copy(X_next)
        allowed_a = np.copy(allowed_a_next)
       

        i += 1  # UPDATE COUNTER FOR NUMBER OF ACTIONS



5
[5.]
3
[3.]
1
[1.]
28
[28.]
10
[10.]


C:\Users\adria\AppData\Local\Temp\ipykernel_59400\4002628119.py:11: RuntimeWarning: overflow encountered in matmul
  Qvalues = np.matmul(W2,X1)+bias_W2
C:\Users\adria\AppData\Local\Temp\ipykernel_59400\3634133120.py:53: RuntimeWarning: invalid value encountered in multiply
  delta =  W2[a,:].reshape(200, 1)*X.reshape(1, 58)
C:\Users\adria\AppData\Local\Temp\ipykernel_59400\4002628119.py:5: RuntimeWarning: invalid value encountered in matmul
  H1 = np.matmul(W1,X)+bias_W1 ## make sure that bias_W1 does not need to be transposed
C:\Users\adria\AppData\Local\Temp\ipykernel_59400\3634133120.py:27: RuntimeWarning: invalid value encountered in matmul
  H = np.matmul(W1,X)+bias_W1


27
[27.]
1
[1.]
18
[18.]
37
[37.]
5
[5.]
5
[5.]
2
[2.]
37
[37.]
5
[5.]
3
[3.]
13
[13.]
14
[14.]
12
[12.]
14
[14.]
1
[1.]
9
[9.]
14
[14.]
1
[1.]
16
[16.]
11
[11.]
19
[19.]
22
[22.]
1
[1.]
21
[21.]
1
[1.]
15
[15.]
19
[19.]
3
[3.]
6
[6.]
1
[1.]
15
[15.]
7
[7.]
14
[14.]
1
[1.]
24
[24.]
36
[36.]
1
[1.]
3
[3.]
15
[15.]
30
[30.]
3
[3.]
7
[7.]
7
[7.]
27
[27.]
1
[1.]
34
[34.]
15
[15.]
15
[15.]
6
[6.]
27
[27.]
1
[1.]
1
[1.]
19
[19.]
31
[31.]
10
[10.]
1
[1.]
1
[1.]
1
[1.]
1
[1.]
45
[45.]
8
[8.]
13
[13.]
21
[21.]
17
[17.]
3
[3.]
19
[19.]
2
[2.]
22
[22.]
11
[11.]
12
[12.]
25
[25.]
12
[12.]
1
[1.]
10
[10.]
10
[10.]
1
[1.]
19
[19.]
15
[15.]
35
[35.]
24
[24.]
1
[1.]
10
[10.]
12
[12.]
4
[4.]
1
[1.]
7
[7.]
7
[7.]
31
[31.]
12
[12.]
7
[7.]
14
[14.]
5
[5.]
3
[3.]
1
[1.]
3
[3.]
45
[45.]
11
[11.]
18
[18.]
3
[3.]
6
[6.]
35
[35.]
2
[2.]
2
[2.]
16
[16.]
22
[22.]
2
[2.]
19
[19.]
4
[4.]
10
[10.]
21
[21.]
3
[3.]
3
[3.]
4
[4.]
9
[9.]
30
[30.]
1
[1.]
1
[1.]
14
[14.]
15
[15.]
1
[1.]
12
[12.]
4
[4.]
1
[1.]
3
[3.]
1
[1